In [1]:
import pandas as pd
import numpy as np
import copy

import matplotlib.pyplot as plt
import seaborn as sns
from IPython.display import clear_output
from PIL import Image
from tqdm import tqdm

import mlflow
import mlflow.pytorch

import torch
from torch.utils.data import Dataset, DataLoader
from torch import nn
from torch.optim import lr_scheduler

from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report
from sklearn.metrics import f1_score

import warnings

sns.set_style('whitegrid')
plt.rcParams.update({'font.size': 15})

%matplotlib inline
%config InlineBackend.figure_formats = ['svg']

warnings.filterwarnings('ignore')

In [2]:
class goodsDataset(Dataset):
    def __init__(self, df, transform=None):
        """
        Arguments:
            df : pandas DataFrame.
            transform (callable, optional): Optional transform to be applied
                on a sample.
        """
        self.data_frame = df
        self.transform = transform

    def __len__(self):
        return self.data_frame.shape[0]

    def __getitem__(self, idx):
        if torch.is_tensor(idx):
            idx = idx.tolist()
        try:
            path = self.data_frame.iloc[idx, 0]
            image = Image.open(path).convert("RGB")

            if self.transform:
                image = self.transform(image)

            label = torch.tensor(self.data_frame.iloc[idx, 1])

            sample = [image, label]
            return sample

        except Exception as e:
            print(f"произошла ошибка в goodsDataset при загрузки картинки: {e}")
            return


def load_data(df,
              transform=None,
              batch_size=4,
              num_workers=0,
              shuffle=True):

    goods_dataset = goodsDataset(df=df, transform=transform)
    dataloader = DataLoader(
        goods_dataset,
        batch_size=batch_size,
        shuffle=shuffle,
        num_workers=num_workers
    )
    return dataloader

def train_model(model,
                train_loader,
                valid_loader,
                criterion,
                optimizer,
                num_epochs,
                name_file_save,
                device='cpu',
                scheduler=None,
                save=True):
    train_losses, train_accuracies = [], []
    valid_losses, valid_accuracies = [], []
    best_accuracy = 0.0
    best_weights = copy.deepcopy(model.state_dict())

    for epoch in range(1, num_epochs + 1):
        train_loss, train_accuracy = 0.0, 0.0
        model.train()
        for images, labels in tqdm(train_loader, desc='Training'):
            images = images.to(device)
            labels = labels.to(device)

            optimizer.zero_grad()
            # images: batch_size x num_channels x height x width
            logits = model(images)
            # logits: batch_size x num_classes
            loss = criterion(logits, labels)
            loss.backward()
            optimizer.step()

            train_loss += loss.item() * images.shape[0]
            train_accuracy += (logits.argmax(dim=1) == labels).sum().item()

        if scheduler is not None:
            scheduler.step()

        train_loss /= len(train_loader.dataset)
        train_accuracy /= len(train_loader.dataset)
        train_losses += [train_loss]
        train_accuracies += [train_accuracy]

        if save:
            mlflow.pytorch.log_model(model, name_file_save)

        true_label = np.array([])
        predict_label = np.array([])
        test_loss, test_accuracy = 0.0, 0.0
        model.eval()
        for images, labels in tqdm(valid_loader, desc='Validating'):
            true_label = np.append(true_label, labels.cpu().numpy())
            images = images.to(device)
            labels = labels.to(device)

            with torch.no_grad():
                logits = model(images)
                # logits: batch_size x num_classes
                loss = criterion(logits, labels)
                probabilities = torch.softmax(logits, dim=1)  # Преобразование логитов в вероятности
                predicted_class = torch.argmax(probabilities, dim=1)
                predict_label = np.append(predict_label, predicted_class.cpu().numpy())

            test_loss += loss.item() * images.shape[0]
            test_accuracy += (logits.argmax(dim=1) == labels).sum().item()

        test_loss /= len(valid_loader.dataset)
        test_accuracy /= len(valid_loader.dataset)
        valid_losses += [test_loss]
        valid_accuracies += [test_accuracy]

        if test_accuracy > best_accuracy:
            best_accuracy = test_accuracy
            best_weights = copy.deepcopy(model.state_dict())

        model.load_state_dict(best_weights)
        if save:
            # torch.save(model.state_dict(), name_file_save + '.pth')
            mlflow.pytorch.log_model(model, name_file_save)

        # plot_losses(train_losses, valid_losses, train_accuracies, valid_accuracies)
        mlflow.log_metrics({"train_losses": train_losses[-1],
                            "valid_losses": valid_losses[-1],
                            "train_accuracies": train_accuracies[-1],
                            "valid_accuracies": valid_accuracies[-1],
                            "f1_score_macro": f1_score(true_label, predict_label, average='macro'),
                            "f1_score_micro": f1_score(true_label, predict_label, average='micro'),
                            "f1_score_weighted": f1_score(true_label, predict_label, average='weighted')},
                           step=epoch)
        # print(classification_report(true_label, predict_label))

    return train_losses, train_accuracies, valid_losses, valid_accuracies

In [3]:
from torchvision.models import ViT_H_14_Weights, vit_h_14
weights = ViT_H_14_Weights.IMAGENET1K_SWAG_E2E_V1
model = vit_h_14(weights=weights)
transform = weights.transforms()
device = torch.device('cuda:1' if torch.cuda.is_available() else 'cpu')
torch.cuda.empty_cache()

In [4]:
df = pd.read_csv("plantdoc_mc_annotation.csv", sep=';').drop('Unnamed: 2', axis=1)
df['id'] = df['id'].apply(lambda x: 'plantsdoc/' + x)
df['classes'] = df['classes'].apply(lambda x: eval(x)[0])
num_classes= df['classes'].unique().shape[0]

# для разметки класссов, на pytorch лучше юзать просто номера
dict_classes = {}
for i, j in enumerate(df['classes'].unique()):
    dict_classes[j] = i

df['classes'] = df['classes'].apply(lambda x: dict_classes[x])

In [5]:
train, valid = train_test_split(df, test_size=0.2, random_state=42)

train_loader = load_data(
    train,
    transform,
    batch_size=10)

valid_loader = load_data(
    valid,
    transform,
    batch_size=10,
    shuffle=False)

# model.fc = nn.Sequential(
#     nn.Linear(3712, 100),
#     nn.Softmax(),
#     nn.Linear(100, num_classes)
# )

# # Замораживаем все слои
# for param in model.parameters():
#     param.requires_grad = False

# # Размораживаем параметры последнего полносвязанного слоя (classifier)
# for param in model.fc.parameters():
#     param.requires_grad = True

# model = model.to(device)


model.heads = nn.Sequential(
    nn.Linear(1280, 100),
    nn.Softmax(),
    nn.Linear(100, num_classes)
)

# Замораживаем все слои
for param in model.parameters():
    param.requires_grad = False

# Размораживаем параметры последнего полносвязанного слоя (classifier)
for param in model.heads.parameters():
    param.requires_grad = True

model = model.to(device)

In [ ]:
criterion = nn.CrossEntropyLoss().to(device)
num_epochs = 10

optimizer = torch.optim.AdamW(model.parameters(), lr=0.001, weight_decay=0.01)

scheduler = lr_scheduler.CosineAnnealingLR(optimizer, T_max=num_epochs, eta_min=0, verbose=True)
experiment_name = "from_VKR"
mlflow.set_experiment(experiment_name)
mlflow.enable_system_metrics_logging()

name_model = "vitH_10_plantdoc"
with mlflow.start_run(run_name=name_model) as run:
    train_losses, train_accuracies, valid_accuracies, valid_accuracies = train_model(
        model,
        train_loader,
        valid_loader,
        criterion,
        optimizer,
        num_epochs,
        name_model,
        device=device,
        scheduler=scheduler,
        save=True
    )

2024/05/31 00:34:24 INFO mlflow.system_metrics.system_metrics_monitor: Started monitoring system metrics.
Training:  13%|█████████████████████▊                                                                                                                                                | 27/206 [07:23<49:04, 16.45s/it]